## Enable the geo-visualization for the dataset

In [1]:
pip install geopandas

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 24.0/24.0 MB 18.3 MB/s eta 0:00:00:00:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 9.6/9.6 MB 15.2 MB/s eta 0:00:0000:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.5/2.5 MB 7.5 MB/s eta 0:00:00ta 0:00:01

[notice] A new release of pip is available: 24.3.1 -> 25.0.1
[notice] To update, run: pip install --upgrade pip
Note: you may need to restart the kernel to use updated packages.


In [2]:
pip install folium

Note: you may need to restart the kernel to use updated packages.


In [4]:
import pandas as pd
import folium

# Load TSV data
haunted_df = pd.read_csv('../Data/haunted_places_with_alcohol_daylight.tsv', sep='\t')

# Initialize the map
m = folium.Map(
    location=[37.8, -96.9],  # Approximate U.S. center
    zoom_start=4,
    tiles='CartoDB Positron'  # Clean basemap
)

# Add simple markers
for idx, row in haunted_df.iterrows():
    folium.CircleMarker(
        location=[row['latitude'], row['longitude']],
        radius=2,  # Tiny dot
        color='red',
        fill=True,
        fill_color='red'
    ).add_to(m)


In [6]:
m

## Add the geometry for haunted houses data
The coordinate system of the dataset is WGS84 which is indiced with 4326

In [8]:
from shapely.geometry import Point
import geopandas as gpd

haunted_gdf = gpd.GeoDataFrame(
    haunted_df,
    geometry=[Point(xy) for xy in zip(haunted_df.longitude, haunted_df.latitude)],
    crs=4326
)

## Add the 1st dataset - Number of religious adherents for each county
This dataset is a combined with two datasets. This first one is the GeoJSON file representing the shapes of all counties in the United States. The second dataset is a census data includes the population(2020), the number of religious adherents (who have a religious faith), and the percentage of that proportion for each county, in .xlsx format. 

### Prepare the combined dataset

In [13]:
# Load counties geo data
counties_gdf = gpd.read_file('../Data/georef-united-states-of-america-county.geojson')
counties_gdf

geo_point_2d  year ste_code  \
0     {'lon': -89.68448923303517, 'lat': 37.38397285...  2023     [29]   
1     {'lon': -92.14706128937199, 'lat': 40.45259555...  2023     [29]   
2     {'lon': -96.1408911702373, 'lat': 40.909732814...  2023     [31]   
3     {'lon': -96.13478658411316, 'lat': 40.64849508...  2023     [31]   
4     {'lon': -97.19390736200879, 'lat': 41.91694582...  2023     [31]   
...                                                 ...   ...      ...   
3230  {'lon': -87.95092905739276, 'lat': 43.38403727...  2023     [55]   
3231  {'lon': -106.79861238121448, 'lat': 42.9621708...  2023     [56]   
3232  {'lon': -168.14474033333335, 'lat': -14.546868...  2023     [60]   
3233  {'lon': -66.42032280982299, 'lat': 18.31712923...  2023     [72]   
3234  {'lon': -67.03843058844521, 'lat': 18.11110693...  2023     [72]   

              ste_name coty_code         coty_name coty_area_code  coty_type  \
0           [Missouri]   [29031]  [Cape Girardeau]            USA     county   
1           [Missouri]   [29199]        [Scotland]            USA     county   
2           [Nebraska]   [31025]            [Cass]            USA     county   
3           [Nebraska]   [31131]            [Otoe]            USA     county   
4           [Nebraska]   [31167]         [Stanton]            USA     county   
...                ...       ...               ...            ...        ...   
3230       [Wisconsin]   [55089]         [Ozaukee]            USA     county   
3231         [Wyoming]   [56025]         [Natrona]            USA     county   
3232  [American Samoa]   [60030]     [Rose Island]            ASM       None   
3233     [Puerto Rico]   [72101]         [Morovis]            PRI  municipio   
3234     [Puerto Rico]   [72125]      [San Germán]            PRI  municipio   

               coty_name_long coty_fp_code coty_gnis_code  \
0     [Cape Girardeau County]          031       00758470   
1           [Scotland County]          199       00758552   
2               [Cass County]          025       00835834   
3               [Otoe County]          131       00835887   
4            [Stanton County]          167       00835905   
...                       ...          ...            ...   
3230         [Ozaukee County]          089       01581105   
3231         [Natrona County]          025       01605077   
3232            [Rose Island]          030       01805243   
3233      [Morovis Municipio]          101       01804531   
3234   [San Germán Municipio]          125       01804543   

                                               geometry  
0     POLYGON ((-89.86112 37.59929, -89.86145 37.525...  
1     POLYGON ((-92.35081 40.59727, -92.35063 40.592...  
2     POLYGON ((-96.46386 41.01607, -96.46371 40.885...  
3     POLYGON ((-96.46376 40.78396, -96.46385 40.653...  
4     POLYGON ((-97.36840 42.09092, -97.36806 42.047...  
...                                                 ...  
3230  POLYGON ((-88.04053 43.54236, -88.04095 43.425...  
3231  POLYGON ((-107.53490 43.50136, -107.53503 43.4...  
3232  POLYGON ((-168.14582 -14.54791, -168.14330 -14...  
3233  POLYGON ((-66.46321 18.37147, -66.46514 18.352...  
3234  POLYGON ((-67.10049 18.10639, -67.10264 18.104...  

[3235 rows x 12 columns]

In [15]:
counties_gdf = counties_gdf.rename(columns={
    'ste_name': 'state',
    'coty_name': 'county'
}).copy()

In [17]:
# I'm doing this step because those fields are String List type instead of String type
counties_gdf['state'] = counties_gdf['state'].apply(lambda x: ' '.join(x) if isinstance(x, list) else str(x))
counties_gdf['county'] = counties_gdf['county'].apply(lambda x: ' '.join(x) if isinstance(x, list) else str(x))

counties_gdf['state'] = counties_gdf['state'].str.strip().str.title()
counties_gdf['county'] = counties_gdf['county'].str.strip().str.title()

In [19]:
# Load Census Data
census_df = pd.read_excel(
    '../Data/2020_USRC_Summaries.xlsx', 
    sheet_name='2020 County Summary'  # Specify the sheet name
).copy()

In [21]:
census_df = census_df.rename(columns={
    'State Name': 'state',
    'County Name': 'county'
})

In [23]:
census_df

FIPS    state           county  2020 Population  Congregations  \
0      01001  Alabama   Autauga County          58805.0          110.0   
1      01003  Alabama   Baldwin County         231767.0          285.0   
2      01005  Alabama   Barbour County          25223.0           93.0   
3      01007  Alabama      Bibb County          22293.0           81.0   
4      01009  Alabama    Blount County          59134.0          145.0   
...      ...      ...              ...              ...            ...   
3140   56041  Wyoming     Uinta County          20450.0           51.0   
3141   56043  Wyoming  Washakie County           7685.0           30.0   
3142   56045  Wyoming    Weston County           6838.0           20.0   
3143     NaN      NaN              NaN              NaN            NaN   
3144  Totals      NaN              NaN      331449281.0       355998.0   

        Adherents  Congregations Per 100,000 Population  \
0         30249.0                            187.058924   
1        124351.0                            122.968326   
2         17330.0                            368.711097   
3         10887.0                            363.342753   
4         33895.0                            245.205804   
...           ...                                   ...   
3140      12710.0                            249.388753   
3141       5098.0                            390.370852   
3142       2473.0                            292.483182   
3143          NaN                                   NaN   
3144  161009516.0                            107.406478   

      Adherents as % of Population  Population Rank  Congregations Rank  \
0                         0.514395            886.0               804.0   
1                         0.536535            296.0               236.0   
2                         0.687071           1595.0               972.0   
3                         0.488360           1699.0              1134.0   
4                         0.573190            882.0               556.0   
...                            ...              ...                 ...   
3140                      0.621516           1795.0              1682.0   
3141                      0.663370           2599.0              2310.0   
3142                      0.361655           2671.0              2705.0   
3143                           NaN              NaN                 NaN   
3144                      0.485774              NaN                 NaN   

      Adherents Rank  Congregations Per 100,000 Pop. Rank  \
0              825.0                               1825.0   
1              264.0                               2478.0   
2             1249.0                                524.0   
3             1675.0                                543.0   
4              747.0                               1317.0   
...              ...                                  ...   
3140          1515.0                               1276.0   
3141          2338.0                                432.0   
3142          2792.0                                943.0   
3143             NaN                                  NaN   
3144             NaN                                  NaN   

      Adherents as % of Population Rank  
0                                1273.0  
1                                1111.0  
2                                 409.0  
3                                1472.0  
4                                 912.0  
...                                 ...  
3140                              657.0  
3141                              483.0  
3142                             2410.0  
3143                                NaN  
3144                                NaN  

[3145 rows x 13 columns]

In [25]:
census_df = census_df.dropna(subset=['state', 'county', '2020 Population', 'Adherents']).copy()
census_df

FIPS    state             county  2020 Population  Congregations  \
0     01001  Alabama     Autauga County          58805.0          110.0   
1     01003  Alabama     Baldwin County         231767.0          285.0   
2     01005  Alabama     Barbour County          25223.0           93.0   
3     01007  Alabama        Bibb County          22293.0           81.0   
4     01009  Alabama      Blount County          59134.0          145.0   
...     ...      ...                ...              ...            ...   
3138  56037  Wyoming  Sweetwater County          42272.0           54.0   
3139  56039  Wyoming       Teton County          23331.0           22.0   
3140  56041  Wyoming       Uinta County          20450.0           51.0   
3141  56043  Wyoming    Washakie County           7685.0           30.0   
3142  56045  Wyoming      Weston County           6838.0           20.0   

      Adherents  Congregations Per 100,000 Population  \
0       30249.0                            187.058924   
1      124351.0                            122.968326   
2       17330.0                            368.711097   
3       10887.0                            363.342753   
4       33895.0                            245.205804   
...         ...                                   ...   
3138    19062.0                            127.744133   
3139    10488.0                             94.295144   
3140    12710.0                            249.388753   
3141     5098.0                            390.370852   
3142     2473.0                            292.483182   

      Adherents as % of Population  Population Rank  Congregations Rank  \
0                         0.514395            886.0               804.0   
1                         0.536535            296.0               236.0   
2                         0.687071           1595.0               972.0   
3                         0.488360           1699.0              1134.0   
4                         0.573190            882.0               556.0   
...                            ...              ...                 ...   
3138                      0.450937           1138.0              1616.0   
3139                      0.449531           1668.0              2628.0   
3140                      0.621516           1795.0              1682.0   
3141                      0.663370           2599.0              2310.0   
3142                      0.361655           2671.0              2705.0   

      Adherents Rank  Congregations Per 100,000 Pop. Rank  \
0              825.0                               1825.0   
1              264.0                               2478.0   
2             1249.0                                524.0   
3             1675.0                                543.0   
4              747.0                               1317.0   
...              ...                                  ...   
3138          1163.0                               2426.0   
3139          1704.0                               2761.0   
3140          1515.0                               1276.0   
3141          2338.0                                432.0   
3142          2792.0                                943.0   

      Adherents as % of Population Rank  
0                                1273.0  
1                                1111.0  
2                                 409.0  
3                                1472.0  
4                                 912.0  
...                                 ...  
3138                             1771.0  
3139                             1781.0  
3140                              657.0  
3141                              483.0  
3142                             2410.0  

[3143 rows x 13 columns]

In [27]:
census_df['county'] = census_df['county'].str.replace(' County', '', regex=False)

census_df['state'] = census_df['state'].str.strip().str.title()
census_df['county'] = census_df['county'].str.strip().str.title()

# Merge County geometries with Census data
counties_merged = counties_gdf.merge(
    census_df,
    on=['state', 'county'],
    how='left'
)

### Join the combined dataset to the haunted houses dataset

In [30]:
# Spatial Join with Counties
joined_df = haunted_gdf.sjoin(
    counties_merged[['geometry', 'county', '2020 Population', 'Adherents', 'Adherents as % of Population']],
    how='left',
    predicate='within'
)

### Calculate and add the field "count of haunted houses per county"

In [33]:
county_counts = joined_df.groupby('county').size().reset_index(name='Haunted Houses Count per County')

# Merge counts back into the main dataset
joined_df = pd.merge(
    joined_df,
    county_counts,
    on='county',
    how='left'
)

### Calculate and add the field "count of haunted houses per 1000 people in the county"

In [34]:
joined_df['Haunted houses per 1000'] = (joined_df['Haunted Houses Count per County'] / joined_df['2020 Population']) * 1000

In [36]:
joined_df.to_csv("../Data/haunted_religious_merged.csv", index="False")

In [38]:
joined_df

city        country  \
0                Ada  United States   
1            Addison  United States   
2             Adrian  United States   
3             Adrian  United States   
4             Albion  United States   
...              ...            ...   
10969    Westminster  United States   
10970    Westminster  United States   
10971    Wheat Ridge  United States   
10972    Wheat Ridge  United States   
10973  Woodland Park  United States   

                                             description  \
0      Ada witch - Sometimes you can see a misty blue...   
1      A little girl was killed suddenly while waitin...   
2      If you take Gorman Rd. west towards Sand Creek...   
3      In the 1970's, one room, room 211, in the old ...   
4      Kappa Delta Sorority - The Kappa Delta Sororit...   
...                                                  ...   
10969  at 12 midnight you can see a lady with two lit...   
10970  Is haunted by the victims of a murder that hap...   
10971  The institution was for kids 18 years old and ...   
10972  Gymnasium -  their have been reports of a litt...   
10973  Cadets from the Air Force Academy participatin...   

                        location     state state_abbrev   longitude  \
0                   Ada Cemetery  Michigan           MI  -85.504893   
1                North Adams Rd.  Michigan           MI  -84.381843   
2                  Ghost Trestle  Michigan           MI  -84.035656   
3       Siena Heights University  Michigan           MI  -84.017565   
4                 Albion College  Michigan           MI  -84.745177   
...                          ...       ...          ...         ...   
10969                  city hall  Colorado           CO -105.048936   
10970             Pillar of Fire  Colorado           CO -105.032091   
10971   Ridge Mental Institution  Colorado           CO -105.063974   
10972  Wheat Ridge Middle School  Colorado           CO -105.103613   
10973         Saylor Park Forest  Colorado           CO -105.022763   

        latitude  city_longitude  city_latitude  ...  Avg_Daylight_Hours  \
0      42.962106      -85.495480      42.960727  ...           11.391667   
1      41.971425      -84.347168      41.986434  ...           11.391667   
2      41.904538      -84.037166      41.897547  ...           11.391667   
3      41.905712      -84.037166      41.897547  ...           11.391667   
4      42.244006      -84.753030      42.243097  ...           11.391667   
...          ...             ...            ...  ...                 ...   
10969  39.862610     -105.037205      39.836653  ...           11.416667   
10970  39.847237     -105.037205      39.836653  ...           11.416667   
10971  39.769726     -105.077206      39.766098  ...           11.416667   
10972  39.764055     -105.077206      39.766098  ...           11.416667   
10973  39.116658     -105.056930      38.993881  ...           11.416667   

       Sunrise_Variability Daylight_Hours_Range                     geometry  \
0                 0.070711             0.016667   POINT (-85.50489 42.96211)   
1                 0.070711             0.016667   POINT (-84.38184 41.97142)   
2                 0.070711             0.016667   POINT (-84.03566 41.90454)   
3                 0.070711             0.016667   POINT (-84.01757 41.90571)   
4                 0.070711             0.016667   POINT (-84.74518 42.24401)   
...                    ...                  ...                          ...   
10969             0.000000             0.000000  POINT (-105.04894 39.86261)   
10970             0.000000             0.000000  POINT (-105.03209 39.84724)   
10971             0.000000             0.000000  POINT (-105.06397 39.76973)   
10972             0.000000             0.000000  POINT (-105.10361 39.76405)   
10973             0.000000             0.000000  POINT (-105.02276 39.11666)   

      index_right     county 2020 Population  Adherents  \
0          1416.0       Kent        6579

## Add the 2nd Dataset - Crime data for each county

This dataset is a combination of `cleaned_crime_data.tsv` with additional data from `joined1.csv`. 

### Merging Details:
- The dataset was merged using **state abbreviations (`state_abbrev`)** and **county names (`county`)**.
- The **crime dataset** provides crime rate statistics per 100,000 people.
- The **joined dataset** includes information about haunted places, alcohol consumption rates, and other relevant attributes.
- A **left join** was used to ensure all haunted places data was retained, while crime data was added where available.

### Additional Columns in the Merged Dataset
After merging, the dataset includes the following newly added columns from `cleaned_crime_data.tsv`:
- **`crime_rate_per_100000`**: Crime rate per 100,000 people in the county.
- **`MURDER`**: Number of reported murder cases.
- **`ROBBERY`**: Number of reported robbery cases.
- **`BURGLRY`**: Number of reported burglary cases.

These columns provide a deeper insight into county-level crime trends, allowing for further analysis of crime rates in relation to haunted places and other factors.

### Source of `cleaned_crime_data.tsv`
The **crime dataset** was sourced from **United States crime rates by county**, which includes county-level crime data in the U.S.  
- **Crime Data (2016):** [ICPSR Crime Data](https://www.icpsr.umich.edu/icpsrweb/)  
- **Population Data (2013):** [U.S. Census](https://census.gov)  
- Original file: `crime_data_w_population_and_crime_rate.csv`

In [2]:
import pandas as pd

# Read cleaned crime data
df_crime = pd.read_csv("../Data/cleaned_crime_data.tsv", sep="\t")

# Read joined data
joined_df = pd.read_csv("../Data/haunted_religious_merged.csv")

# Ensure 'county' column does not contain the suffix "county"
df_crime["county"] = df_crime["county"].str.replace(r"\s*county\s*$", "", case=False, regex=True)
joined_df["county"] = joined_df["county"].str.replace(r"\s*county\s*$", "", case=False, regex=True)

# Perform a left join, keeping all haunted places data
joined_df = pd.merge(
    joined_df,
    df_crime,
    how="left",  # Preserve all haunted places data
    left_on=["state_abbrev", "county"],  # Key from Haunted Places dataset
    right_on=["state_abbrev", "county"]  # Key from Crime dataset
)

# Save the merged dataset
joined_df.to_csv("../Data/haunted_religious_crime_merged.csv", index=False)

# Display the first few rows to check merge results
print(joined_df.columns)
print(joined_df.head())

Index(['Unnamed: 0', 'city', 'country', 'description', 'location', 'state',
       'state_abbrev', 'longitude', 'latitude', 'city_longitude',
       'city_latitude', 'audio evidence', 'image/video/visual evidence',
       'haunted places date', 'haunted places witness count', 'time of day',
       'apparition type', 'event type', 'binge drinking rate (%)',
       'median drinks per binge (overall)',
       'median drinks per binge (25% most active)',
       'binge frequency (monthly overall)',
       'binge frequency (monthly 25% most active)', 'annual deaths',
       '5-year excess death increase (%)', 'death ratio (1 per x adults)',
       'deaths per 10k adults', '% male deaths', '% chronic causes deaths',
       '% deaths in adults 35+', '% under 21 deaths',
       'cdc years of potential life lost',
       'taxpayer spending 2010 (billion usd)',
       'adjusted spending 2022 (billion usd)', 'cost per drink (usd)',
       'Avg_Daylight_Hours', 'Sunrise_Variability', 'Daylight_Hour

In [3]:
joined_df

Unnamed: 0           city        country  \
0               0            Ada  United States   
1               1        Addison  United States   
2               2         Adrian  United States   
3               3         Adrian  United States   
4               4         Albion  United States   
...           ...            ...            ...   
10969       10969    Westminster  United States   
10970       10970    Westminster  United States   
10971       10971    Wheat Ridge  United States   
10972       10972    Wheat Ridge  United States   
10973       10973  Woodland Park  United States   

                                             description  \
0      Ada witch - Sometimes you can see a misty blue...   
1      A little girl was killed suddenly while waitin...   
2      If you take Gorman Rd. west towards Sand Creek...   
3      In the 1970's, one room, room 211, in the old ...   
4      Kappa Delta Sorority - The Kappa Delta Sororit...   
...                                                  ...   
10969  at 12 midnight you can see a lady with two lit...   
10970  Is haunted by the victims of a murder that hap...   
10971  The institution was for kids 18 years old and ...   
10972  Gymnasium -  their have been reports of a litt...   
10973  Cadets from the Air Force Academy participatin...   

                        location     state state_abbrev   longitude  \
0                   Ada Cemetery  Michigan           MI  -85.504893   
1                North Adams Rd.  Michigan           MI  -84.381843   
2                  Ghost Trestle  Michigan           MI  -84.035656   
3       Siena Heights University  Michigan           MI  -84.017565   
4                 Albion College  Michigan           MI  -84.745177   
...                          ...       ...          ...         ...   
10969                  city hall  Colorado           CO -105.048936   
10970             Pillar of Fire  Colorado           CO -105.032091   
10971   Ridge Mental Institution  Colorado           CO -105.063974   
10972  Wheat Ridge Middle School  Colorado           CO -105.103613   
10973         Saylor Park Forest  Colorado           CO -105.022763   

        latitude  city_longitude  ...  index_right     county  \
0      42.962106      -85.495480  ...       1416.0       Kent   
1      41.971425      -84.347168  ...       2347.0  Hillsdale   
2      41.904538      -84.037166  ...        173.0    Lenawee   
3      41.905712      -84.037166  ...        173.0    Lenawee   
4      42.244006      -84.753030  ...        596.0    Calhoun   
...          ...             ...  ...          ...        ...   
10969  39.862610     -105.037205  ...       1136.0      Adams   
10970  39.847237     -105.037205  ...       1136.0      Adams   
10971  39.769726     -105.077206  ...         64.0  Jefferson   
10972  39.764055     -105.077206  ...         64.0  Jefferson   
10973  39.116658     -105.056930  ...       1369.0    El Paso   

       2020 Population Adherents  Adherents as % of Population  \
0             657974.0  282420.0                      0.429227   
1              45746.0   11128.0                      0.243256   
2              99423.0   33427.0                      0.336210   
3              99423.0   33427.0                      0.336210   
4             134310.0   43340.0                      0.322686   
...                ...       ...                           ...   
10969         519572.0  139606.0                      0.268694   
10970         519572.0  139606.0                      0.268694   
10971         582910.0  181477.0                      0.311329   
10972         582910.0  181477.0                      0.311329   
10973         730395.0  315765.0                      0.432321   

      Haunted Houses Count per County crime_rate_per_100000 MURDER  ROBBERY  \
0                                46.0            395.689239   22.0    639.0   
1                                 3.0            190.885230    0.0      2.0   
2        

Extract usefull historical places from the extracted.gdb files

## Add the 3rd dataset - Nearest historic sites for each haunted house

In [ ]:
pip install pyogrio

In [1]:
# Import Libraries
import pyogrio
import pandas as pd
import geopandas as gpd

Specify file paths
Specify the input geodatabase (GDB) file path and output CSV file path.

In [2]:
gdb_path = "../Data/extracted_gdb/NRIS_CR_Standards_Public.gdb"
output_csv_path = "../Data/historic_sites.csv"

List the layers in the GDB that contain useful historical site names

In [3]:
layers_to_extract = [
    ("crstru_pt", "RESNAME"), ("crstru_py", "RESNAME"),
    ("crbldg_pt", "RESNAME"), ("crbldg_py", "RESNAME"),
    ("crdist_py", "RESNAME"), ("crobj_pt", "RESNAME")
]

## Extract Data from Layers
Loop through each layer, read the data, and extract relevant columns.
- Standardize the Site_Name column
- Convert SRC_DATE to Year_Recorded if available
- Handle errors if a layer cannot be loaded

In [4]:
historic_sites = []

for layer, name_column in layers_to_extract:
    try:
        df = pyogrio.read_dataframe(gdb_path, layer=layer)
        if name_column in df.columns:
            # Extract relevant columns
            cols_to_keep = [name_column, "geometry"]
            if "SRC_DATE" in df.columns:
                cols_to_keep.append("SRC_DATE")  # Keep source date if available

            df = df[cols_to_keep].dropna(subset=[name_column])  # Drop rows without site names
            df.rename(columns={name_column: "Site_Name"}, inplace=True)  # Standardize column name

            # Convert SRC_DATE to Year (if available)
            if "SRC_DATE" in df.columns:
                df["Year_Recorded"] = pd.to_datetime(df["SRC_DATE"], errors="coerce").dt.year
                df.drop(columns=["SRC_DATE"], inplace=True)  # Remove raw date column

            historic_sites.append(df)
            print(f"Successfully extracted {len(df)} site names from {layer}")

    except Exception as e:
        print(f"Error loading layer {layer}: {e}")

Successfully extracted 4595 site names from crstru_pt
Successfully extracted 415 site names from crstru_py
Successfully extracted 58442 site names from crbldg_pt
Successfully extracted 4943 site names from crbldg_py
Successfully extracted 12281 site names from crdist_py
Successfully extracted 415 site names from crobj_pt


Combine layers into a dataframe, extract the features, and save it to the new csv file

In [5]:
# Combine all layers into a single DataFrame
historic_gdf = gpd.GeoDataFrame(pd.concat(historic_sites), geometry="geometry", crs="EPSG:4326")

# Convert all non-Point geometries to their center point (centroid)
historic_gdf["geometry"] = historic_gdf.geometry.apply(lambda geom: geom.centroid if not geom.geom_type == "Point" else geom)

# Extract longitude & latitude
historic_gdf["longitude"] = historic_gdf.geometry.x
historic_gdf["latitude"] = historic_gdf.geometry.y

# Drop the geometry column since CSV doesn't support it
historic_gdf.drop(columns=["geometry"], inplace=True)

# Save as CSV
historic_gdf.to_csv(output_csv_path, index=False)

print(f"\nAll historic sites saved to: {output_csv_path}")


All historic sites saved to: ../Data/historic_sites.csv


### Add 3 New Columns to the Dataset

In [6]:
pip install rtree


[notice] A new release of pip is available: 24.3.1 -> 25.0.1
[notice] To update, run: pip install --upgrade pip
Note: you may need to restart the kernel to use updated packages.


# Define File Paths and Load Data

Load Haunted Places data and convert everything to GDFs

In [7]:
from shapely.geometry import Point
from rtree import index

# File paths
haunted_path = "../Data/haunted_places.csv"
historical_sites_path = "../Data/historic_sites.csv"
joined1_path = "../Data/haunted_religious_crime_merged.csv"  # Load the existing file

# Load Haunted Places CSV
haunted_df = pd.read_csv(haunted_path)

# Convert haunted places to GeoDataFrame
haunted_df["geometry"] = haunted_df.apply(
    lambda row: Point(row["longitude"], row["latitude"])
    if pd.notnull(row["longitude"]) and pd.notnull(row["latitude"]) else None,
    axis=1
)

haunted_gdf = gpd.GeoDataFrame(haunted_df, geometry="geometry", crs="EPSG:4326")

# Load Historical Sites CSV
historical_df = pd.read_csv(historical_sites_path)

# Convert historical sites to GeoDataFrame
historical_df["geometry"] = historical_df.apply(
    lambda row: Point(row["longitude"], row["latitude"])
    if pd.notnull(row["longitude"]) and pd.notnull(row["latitude"]) else None,
    axis=1
)

historical_gdf = gpd.GeoDataFrame(historical_df, geometry="geometry", crs="EPSG:4326")

Define Search Radius for Column

In [8]:
# Convert miles to degrees (~1 mile ≈ 0.0145 degrees)
search_radius_deg = 5 * 0.0145

## Find Nearest Historical Site and Count Nearby Sites
For each haunted place:
- Find all historical sites within 5 miles.
- Identify the nearest historical site.
- Count the number of historical sites within 5 miles.

In [9]:
# Create a spatial index for historical sites
historical_idx = index.Index()
for i, geom in enumerate(historical_gdf.geometry):
    historical_idx.insert(i, geom.bounds)

# Initialize new columns
haunted_gdf["nearest_historical_place"] = None
haunted_gdf["num_historical_places_5mi"] = 0
haunted_gdf["year_of_nearest_historical_place"] = None

# Find nearest historical place and count nearby ones
for idx, row in haunted_gdf.iterrows():
    if row.geometry:  # Ensure valid geometry
        # Find possible matches using the spatial index
        possible_matches = list(historical_idx.intersection(row.geometry.buffer(search_radius_deg).bounds))

        # Find the nearest site
        nearest_site = None
        min_distance = float("inf")
        num_nearby_sites = 0

        for i in possible_matches:
            site = historical_gdf.iloc[i]
            distance = row.geometry.distance(site.geometry)

            # Count number of historical sites within 5 miles
            if distance <= search_radius_deg:
                num_nearby_sites += 1

            # Find the closest historic site
            if distance < min_distance:
                min_distance = distance
                nearest_site = site

        # Assign values if a nearest site was found
        if nearest_site is not None:
            haunted_gdf.at[idx, "nearest_historical_place"] = nearest_site["Site_Name"]
            haunted_gdf.at[idx, "year_of_nearest_historical_place"] = nearest_site["Year_Recorded"]

        # Assign the count of nearby sites
        haunted_gdf.at[idx, "num_historical_places_5mi"] = num_nearby_sites

## Prepare Data for Merging
Drop the geometry column as it is not needed in the final CSV.


In [10]:
haunted_gdf.drop(columns=["geometry"], inplace=True)

## Load and Merge with Existing Dataset
Read the existing joined1.csv file and merge the new columns from haunted_gdf

Write the merged dataset back to joined1.csv

In [13]:
# Load joined1.csv
joined1_df = pd.read_csv(joined1_path)

# Merge the new columns from haunted_gdf into joined1_df (assuming they share a unique key like 'id')
# If no unique key exists, merging will have to be done carefully
merged_df = joined1_df.merge(
    haunted_gdf[["nearest_historical_place", "num_historical_places_5mi", "year_of_nearest_historical_place"]],
    left_index=True, right_index=True, how="left"
)

# Save the updated file back to joined1.csv
merged_df.to_csv("../Data/haunted_religious_historic_crime_merged.tsv", index=False, sep='\t')

print(f"\n Created haunted_religious_historic_crime_merged.tsv with new added columns")


 Created haunted_religious_historic_crime_merged.tsv with new added columns
